In [1]:
from src.submission.check_validity import is_model_on_hub
from huggingface_hub import HfApi
import re

/Users/haoyang/miniconda3/envs/llm_reason/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
still_on_hub, _, model_config = is_model_on_hub(
    "01-ai/Yi-34B-Chat", "main", trust_remote_code=True, test_tokenizer=False
)
getattr(model_config, "torch_dtype", None)

torch.bfloat16

In [5]:
open_models = {
    "Yi-34b": "01-ai/Yi-34B-Chat",
    "Mistral-7b": "mistralai/Mistral-7B-Instruct-v0.1",
    "Vicuna-13b": "lmsys/vicuna-13b-v1.3",
    "Phi-1.5": "microsoft/phi-1_5",
    "MPT-30b": "mosaicml/mpt-30b-instruct",
    "Phi-2": "microsoft/phi-2",
    "Qwen-14b": "Qwen/Qwen-14B-Chat"
}

api = HfApi()
size_pattern = size_pattern = re.compile(r"(\d\.)?\d+(b|m)")

new_params = {}

for model_name, model_id in open_models.items():
    still_on_hub, _, model_config = is_model_on_hub(
        model_id, "main", trust_remote_code=True, test_tokenizer=False
    )
    precision = str(getattr(model_config, "torch_dtype", None))

    print(f"{model_name} is on hub: {still_on_hub}")
    print(f"{model_name} config: {precision}")

    model_info = api.model_info(repo_id=model_id, revision="main")
    try:
        model_size = round(model_info.safetensors["total"] / 1e9, 3)
    except (AttributeError, TypeError):
        try:
            size_match = re.search(size_pattern, model_info.modelId.lower())
            model_size = size_match.group(0)
            model_size = round(float(model_size[:-1]) if model_size[-1] == "b" else float(model_size[:-1]) / 1e3, 3)
        except AttributeError:
            model_size = "N/A"
    print(f"{model_name} size: {model_size}")
    new_params[model_name] = (precision, model_size)

Yi-34b is on hub: True
Yi-34b config: torch.bfloat16
Yi-34b size: 34.389
Mistral-7b is on hub: True
Mistral-7b config: torch.bfloat16
Mistral-7b size: 7.242
Vicuna-13b is on hub: True
Vicuna-13b config: torch.float16
Vicuna-13b size: 13.0
Phi-1.5 is on hub: True
Phi-1.5 config: torch.float16
Phi-1.5 size: N/A


/Users/haoyang/.cache/huggingface/modules/transformers_modules/mosaicml/mpt-30b-instruct/56bcbea5361d8381c297ca51c02ee5b6f0415cb4/configuration_mpt.py:97: UserWarning: alibi is turned on, setting `learned_pos_emb` to `False.`
  warnings.warn(f'alibi is turned on, setting `learned_pos_emb` to `False.`')


MPT-30b is on hub: True
MPT-30b config: torch.bfloat16
MPT-30b size: 30.0
Phi-2 is on hub: True
Phi-2 config: torch.float16
Phi-2 size: 2.78
Qwen-14b is on hub: True
Qwen-14b config: None
Qwen-14b size: 14.167


In [6]:
new_params

{'Yi-34b': ('torch.bfloat16', 34.389),
 'Mistral-7b': ('torch.bfloat16', 7.242),
 'Vicuna-13b': ('torch.float16', 13.0),
 'Phi-1.5': ('torch.float16', 'N/A'),
 'MPT-30b': ('torch.bfloat16', 30.0),
 'Phi-2': ('torch.float16', 2.78),
 'Qwen-14b': ('None', 14.167)}